In [1]:
###Python Packages###

import numpy as np
import matplotlib.pyplot as plt
from matplotlib import rc
from matplotlib.colors import LogNorm
import math as mth

import timeit
import ODE_utils as odeu
from scipy import optimize
import tables
#from mpmath import *


In [2]:
###Initial Values###

M0=1.0
Q=0.95
Lambda=0.01#0.1
scalarfield=True
A=.1#.115
vscalarfield=False


In [3]:
Tol=.5
N=200
Nul=N
Nup=10**(40)
scal=10
umax=13
vmax=20
datatype=np.float64


#ru0=5.0
#dr0v=.4
ru0=5.0
#dr0v=0.045
dr0v=-1/(4*-.375)*(1-2*M0/ru0+Q**2/ru0**2-Lambda*ru0**2/3)
#dr0v=0.045

bdytype="stan"
scaltostan=False
solveaffine=False

Elist=[1]
#Elist=[1,2,4,8,16]

#uloc=[1/8,1/4,3/8,1/2,5/8]
#uloc=[1/5,2/5,3/5,4/5,9/10]
uloc=[8.2/10]

In [4]:
###Defining Needed Constants###

scalf=float(scal)
u0=0.0
v0=0.0
rv0=ru0
phiu0=0.0
phiv0=0.0

if M0==0.0:
    dv0=1/N    
else:
    dv0=M0/N
    


def fr(r,M0,Q,Lambda):
    return 1-2*M0/r+Q**2.0/r**2.0-Lambda*r**2.0/3.0

if Lambda>0 or Lambda<0:
    sol = optimize.root(fr,[0.687,1.3,50.0],args=(M0,Q,Lambda), method='hybr')
    rminus=sol.x[0]
    rplus=sol.x[1]
    rcosm=sol.x[2]
else:
    rplus=M0+(M0**2-Q**2)**(.5)
    rminus=M0-(M0**2-Q**2)**(.5)
    rcosm=0.0
    

wHD=True 

print("r+: "+str(rplus))
print("r-: "+str(rminus))
print("rc: "+str(rcosm))

print("Max r along u=0: "+str(ru0+vmax*dr0v))
###Predicting Run time###

###timer
start = timeit.default_timer()

Nu=Nul*umax*100#int(umax/du0)
Nv=int(vmax/dv0)
#print("Number of points for lowest iteration is "+str(Nu*Nv)+","+str(Nu)+"X"+str(Nv))
print("Number of points for highest iteration is "+str(Nu*Nv*max(Elist)**2)+","+str(Nu*max(Elist))+"X"+str(Nv*max(Elist)))

numpoints=0.0
for i in range(0,len(Elist)):
    numpoints=Elist[i]**2.0*Nu*Nv+numpoints
print("Total number of points is "+str(int(numpoints)))

predtime=numpoints/(78000)

print("Runtime: about "+str(format(predtime/60,'.2f'))+" minutes")


r+: 1.3284533330414854
r-: 0.6865663660958411
rc: 16.251309434683154
Max r along u=0: 12.370222222222221
Number of points for highest iteration is 1040000000,260000X4000
Total number of points is 1040000000
Runtime: about 222.22 minutes


In [5]:
##################################
###Applying Boundary Conditions###

Emax=max([Elist])


rnpf=np.zeros((2,Nv),dtype=datatype)
signpf=np.zeros((2,Nv),dtype=datatype)
phinpf=np.zeros((2,Nv),dtype=datatype)
drnpvf=np.zeros((2,Nv),dtype=datatype)
dsignpvf=np.zeros((2,Nv),dtype=datatype)
dphinpvf=np.zeros((2,Nv),dtype=datatype)
drnpuf=np.zeros((2,Nv),dtype=datatype)
dsignpuf=np.zeros((2,Nv),dtype=datatype)
dphinpuf=np.zeros((2,Nv),dtype=datatype)
massnpf=np.full((2,Nv),M0)#np.zeros((2,Nv))
#drunpv=np.full((1,Nv-1),-1/(4*dr0v)*(1-2*M0/ru0+Q**2/ru0**2))
 


rnpf[0], signpf[0], phinpf[0] , drnpvf[0], dsignpvf[0], dphinpvf[0], drnpuf[0], dsignpuf[0], dphinpuf[0] = odeu.boundaryv(scal,bdytype,Nv,ru0,dr0v,dv0,vmax,M0,Q,Lambda,scalarfield,A,datatype)
massnpf[0]=M0

print(dsignpuf[0])

Using Standard Coordinates Along V
[0.00000000e+00 3.74892106e-05 7.49501995e-05 ... 9.27605473e-02
 9.27746391e-02 9.27887288e-02]


In [6]:
drunptemp=np.empty((Nv))*np.nan
#dsigunp=np.empty((Nu))*np.nan


A=.115
u1=9.5
u2=10

###Applying Propagation Algorithm###

urange=np.array([0.0],dtype=datatype)

massnpf[0][0]=1.0

#drunp[0]=-mth.exp(signpf[0][0])/(4.0*dr0v)*(1-2*M0/ru0+Q**2.0/ru0**2.0-Lambda*ru0**2/3)
#dsigunpvalue=100*np.exp(np.nanmax(signpf))
#drunptemp=drunp[0]
    

i=0
dv=dv0
if M0>0:
    du0=M0/Nul
elif M0==0:
    du0=1/Nul

du=du0

###fix this part (put in front of boundary conditions so it is an initial condition)
#if bdytype=="edd" or bdytype=="fulledd":
    #bdyvalue=1.0
    #dsignpuf[0]=2*(3*Q**2-3*M0*ru0+ru0**4*Lambda)/(ru0*(-3*Q**2+ru0*(6*M0-3*ru0+ru0**3*Lambda)))*drunp[0]
    #dsigunp[0]=2.0*(M0*rnpf[0]-Q**2.0)/(rnpf[0]*(Q**2.0+rnpf[0]*(-2*M0+rnpf[0])))*drunp[0]
#else:
    #bdyvalue=0.0
    #dsigunp[0]=0.0
######
    
atom = tables.Float64Atom()

rnpfile = tables.open_file('rnp.h5', mode='w',encoding="utf8") 
rnp = rnpfile.create_earray(rnpfile.root, 'data', atom, (0, Nv))

signpfile = tables.open_file('signp.h5', mode='w',encoding="utf8") 
signp = signpfile.create_earray(signpfile.root, 'data', atom, (0, Nv))
phinpfile = tables.open_file('phinp.h5', mode='w',encoding="utf8") 
phinp = phinpfile.create_earray(phinpfile.root, 'data', atom, (0, Nv))
massnpfile = tables.open_file('massnp.h5', mode='w',encoding="utf8") 
massnp = massnpfile.create_earray(massnpfile.root, 'data', atom, (0, Nv))
    
 
#rtemp=rnpf[0]   
#print(rtemp)
rnp.append(rnpf[0].reshape(1,Nv))
signp.append(signpf[0].reshape(1,Nv))
phinp.append(phinpf[0].reshape(1,Nv))
massnp.append(massnpf[0].reshape(1,Nv))

#drunp=np.append(drunp,np.nan)
#dsigunp=np.append(dsigunp,np.nan)
#dphinpuf=np.append(dphinpuf,np.nan)
drunptemp=np.nanmax(np.abs(drnpuf[0]))     
dsigunpvalue=np.nanmax(np.abs(dsignpuf[0]))
dphiutemp=np.nanmax(np.abs(dphinpuf[0]))

rnpf[1][0]=rnpf[0][0]

i=0
TempTol=1 
TempTolv=1
Eres=False
while max(urange)<umax and i<50000 and rnpf[1][0]>0.0 and du>0.0:

    
    du=du0*Tol*TempTol/max([abs(dsigunpvalue),abs(drunptemp),abs(dphiutemp)])

    
    if du<1/Nup*1.1:
        du=1/Nup
     
    
    if du>=1/Nul:
        #print('r='+str(rnpf[i][0]))
        if rnpf[1][0]<rplus:
            du=1/(1*Nul)
            #print(rplus)
        else:
            du=1/Nul
    

    print("%.24f" % urange[i])
    print("%.24f" % du)
    
    ###fix this section (dphinpuf is in the wrong form)
    #if urange[i]>u1 and urange[i]<u2 and vscalarfield==True:
        #u=urange[i]+du
        #phinpf[1][0]=A*64*(u-u1)**3.0*(u2-u)**3.0/(u2-u1)**6.0
        #dphinpuf[i]=192*A*(u-u1)**2.0*(u-u2)**2.0*(-2*u+u1+u2)/(u1-u2)**6.0 
    #else:
        #continue
        #phinpf[1][0]=0.0
        #dphinpuf[i+1]=0.0
    

    ###Predictor###
    drnpvf[1]=drnpvf[0]+du*odeu.Rfunc(drnpvf[0],drnpuf[0],rnpf[0],signpf[0],Q,Lambda)
    dsignpvf[1]=dsignpvf[0]+du*odeu.Sigfunc(drnpvf[0],drnpuf[0],dphinpuf[0],dphinpvf[0],rnpf[0],signpf[0],Q)
    dphinpvf[1]=dphinpvf[0]+du*odeu.Phifunc(drnpvf[0],drnpuf[0],dphinpuf[0],dphinpvf[0],rnpf[0])
    drnpuf[1]=drnpuf[0]+du*odeu.Coneq(drnpuf[0],dsignpuf[0],dphinpuf[0],rnpf[0])#(drnpuf[0]*dsignpuf[0]-rnpf[0]*np.power(dphinpuf[0],2.0))
    
    rnpf[1]=rnpf[0]+1/2*du*(drnpuf[0]+drnpuf[1])
    signpf[1]=signpf[0]+du*dsignpuf[0]
    phinpf[1]=phinpf[0]+du*dphinpuf[0]
    
     
    if any(phinpf[1]):
        dsignpuf[1][0]=0.0
        dphinpuf[1][0]=0.0
        for j in range(0,Nv-1):
            dphinpuf[1][j+1]=dphinpuf[1][j]+dv*odeu.Phifunc(drnpvf[1][j],drnpuf[1][j],dphinpuf[1][j],dphinpvf[1][j],rnpf[1][j])         
            dphinpuf[1][j+1]=dphinpuf[1][j]+1/2*dv*(odeu.Phifunc(drnpvf[1][j],drnpuf[1][j],dphinpuf[1][j],dphinpvf[1][j],rnpf[1][j])+odeu.Phifunc(drnpvf[1][j+1],drnpuf[1][j+1],dphinpuf[1][j+1],dphinpvf[1][j+1],rnpf[1][j+1]))
            #dsignpuf[1][j+1]=dsignpuf[1][j]+dv*odeu.Sigfunc(drnpvf[1][j],drnpuf[1][j],dphinpuf[1][j],dphinpvf[1][j], rnpf[1][j],signpf[1][j],Q)                                                                             
            #Phifuncnp=odeu.Phifunc(drnpvf[1],drnpuf[1],dphinpuf[1],dphinpvf[1],rnpf[1])
    else:
        dphinpuf[1]=0.0
    Sigfuncnp=odeu.Sigfunc(drnpvf[1],drnpuf[1],dphinpuf[1],dphinpvf[1],rnpf[1],signpf[1],Q)
    dsignpuf[1]=dsignpuf[1][0]+1/2*dv*(np.cumsum(Sigfuncnp+np.roll(Sigfuncnp,-1))-(Sigfuncnp+np.roll(Sigfuncnp,-1)))
    #drnpuf[1]=drnpuf[0]+1/2*du*(odeu.Coneq(drnpuf[0],dsignpuf[0],dphinpuf[0],rnpf[0])+odeu.Coneq(drnpuf[1],dsignpuf[1],dphinpuf[1],rnpf[1]))
    #signpf[1]=signpf[0]+1/2*du*(dsignpuf[0]+dsignpuf[1])
    
    ###Correction###
    drnpvf[1]=drnpvf[0]+1/2*du*(odeu.Rfunc(drnpvf[0],drnpuf[0],rnpf[0],signpf[0],Q,Lambda)+odeu.Rfunc(drnpvf[1],drnpuf[1],rnpf[1],signpf[1],Q,Lambda))
    dsignpvf[1]=dsignpvf[0]+1/2*du*(odeu.Sigfunc(drnpvf[0],drnpuf[0],dphinpuf[0],dphinpvf[0],rnpf[0],signpf[0],Q)+odeu.Sigfunc(drnpvf[1],drnpuf[1],dphinpuf[1],dphinpvf[1],rnpf[1],signpf[1],Q))
    dphinpvf[1]=dphinpvf[0]+1/2*du*(odeu.Phifunc(drnpvf[0],drnpuf[0],dphinpuf[0],dphinpvf[0],rnpf[0])+odeu.Phifunc(drnpvf[1],drnpuf[1],dphinpuf[1],dphinpvf[1],rnpf[1]))
    drnpuf[1]=drnpuf[0]+1/2*du*(odeu.Coneq(drnpuf[0],dsignpuf[0],dphinpuf[0],rnpf[0])+odeu.Coneq(drnpuf[1],dsignpuf[1],dphinpuf[1],rnpf[1]))
    
    rnpf[1]=rnpf[0]+1/2*du*(drnpuf[0]+drnpuf[1])
    signpf[1]=signpf[0]+1/2*du*(dsignpuf[0]+dsignpuf[1])
    phinpf[1]=phinpf[0]+1/2*du*(dphinpuf[0]+dphinpuf[1])
    

    if np.any(phinpf[1]): 
        dsignpuf[1][0]=0.0
        dphinpuf[1][0]=0.0
        for j in range(0,Nv-1):
            dphinpuf[1][j+1]=dphinpuf[1][j]+1/2*dv*(odeu.Phifunc(drnpvf[1][j],drnpuf[1][j],dphinpuf[1][j],dphinpvf[1][j],rnpf[1][j])+odeu.Phifunc(drnpvf[1][j+1],drnpuf[1][j+1],dphinpuf[1][j+1],dphinpvf[1][j+1],rnpf[1][j+1]))         
            #dsignpuf[1][j+1]=dsignpuf[1][j]+1/2*dv*(odeu.Sigfunc(drnpvf[1][j],drnpuf[1][j],dphinpuf[1][j],dphinpvf[1][j],rnpf[1][j],signpf[1][j],Q)+odeu.Sigfunc(drnpvf[1][j+1],drnpuf[1][j+1],dphinpuf[1][j+1],dphinpvf[1][j+1],rnpf[1][j+1],signpf[1][j+1],Q))    
    else:
        dphinpuf[1]=0.0
    Sigfuncnp=odeu.Sigfunc(drnpvf[1],drnpuf[1],dphinpuf[1],dphinpvf[1],rnpf[1],signpf[1],Q)
    dsignpuf[1]=dsignpuf[1][0]+1/2*dv*(np.cumsum(Sigfuncnp+np.roll(Sigfuncnp,-1))-(Sigfuncnp+np.roll(Sigfuncnp,-1)))
    
    
    massnpf[1]=(1+4.0*np.exp(-signpf[1])*drnpuf[1]*drnpvf[1])*rnpf[1]/2.0+np.power(Q,2.0)/(2.0*rnpf[1])-Lambda*np.power(rnpf[1],3.0)/6.0
    
    drunptemp=np.nanmax(np.abs(drnpuf[1]))      
    dsigunpvalue=np.nanmax(np.abs(dsignpuf[1]))    
    dphiutemp=np.nanmax(np.abs(dphinpuf[1]))
    #if any(abs((np.exp(signpf[0][:])-np.exp(signpf[1][:]))/np.exp(signpf[0][:]))>0.01):  
    if float(dsigunpvalue*du)>1000:#0.1:
        TempTol=TempTol/2
        Eres=True
    else:
        
        if urange[i]+du<umax:
            urange=np.append(urange,urange[i]+du)
        else:
            break
        
        rnp.append(rnpf[1].reshape(1,Nv))
        signp.append(signpf[1].reshape(1,Nv))
        phinp.append(phinpf[1].reshape(1,Nv))
        massnp.append(massnpf[1].reshape(1,Nv))
    
        #drunp=np.append(drunp,np.nan)
        #dsigunp=np.append(dsigunp,np.nan)
        #dphinpuf=np.append(dphinpuf,np.nan)
    
        rnpf[0]=rnpf[1]
        phinpf[0]=phinpf[1]
        signpf[0]=signpf[1]
        drnpvf[0]=drnpvf[1]
        dsignpvf[0]=dsignpvf[1]
        dphinpvf[0]=dphinpvf[1]
        drnpuf[0]=drnpuf[1]
        dsignpuf[0]=dsignpuf[1]
        dphinpuf[0]=dphinpuf[1]
        massnpf[0]=massnpf[1]
    
        
        
        if Eres==True:
            TempTol=2*TempTol
        else:
            TempTol=1
        Eres=False
        i+=1
    
    #print(TempTol)
    print(drnpuf[1][-1])
    print(dsignpuf[1][-1])
    print(massnpf[1][-1])
    #print(dphinpuf[1][-1])
    print('---')
    
    #drunp=np.insert(drunp,(1)*Nv,np.empty((Nv))*np.nan).reshape(i+2,Nv)
    #dsigunp=np.insert(dsigunp,(1)*Nv,np.empty((Nv))*np.nan).reshape(i+2,Nv)
    #dphinpuf=np.insert(dphinpuf,(1),np.empty((1))*np.nan).reshape(i+2)
    #print(urange)
     
    #print(urange)
  
    
    #du=abs(du0*Tol/np.nanmin(drunptemp))

    
    
    
    
    #if rnpf[1][0]<0.0 or np.isnan(du):
        #break
   
    #dumaxlist=[]
    
    
    #if i>1000:
        #break


0.000000000000000000000000
0.005000000000000000104083
-0.33777937619269754
0.09285786044688607
1.4789131254847843
---
0.005000000000000000104083
0.005000000000000000104083
-0.33793629871021436
0.09292709131974053
1.4789131240176687
---
0.010000000000000000208167
0.005000000000000000104083
-0.3380934112497902
0.0929964244344452
1.4789131225421552
---
0.014999999999999999444888
0.005000000000000000104083
-0.33825071418174907
0.0930658600027708
1.478913121058205
---
0.020000000000000000416334
0.005000000000000000104083
-0.3384082078773857
0.09313539823705275
1.4789131195657872
---
0.025000000000000001387779
0.005000000000000000104083
-0.3385658927089686
0.09320503935019459
1.4789131180648656
---
0.030000000000000002359224
0.005000000000000000104083
-0.33872376904974333
0.09327478355567262
1.4789131165554066
---
0.035000000000000003330669
0.005000000000000000104083
-0.3388818372739358
0.09334463106753138
1.4789131150373735
---
0.040000000000000000832667
0.005000000000000000104083
-0.339040

-0.34958662513850575
0.09811705351936505
1.4789129962234842
---
0.365000000000000213162821
0.005000000000000000104083
-0.34975823714115845
0.09819422290357736
1.4789129940572674
---
0.370000000000000217603713
0.005000000000000000104083
-0.34993006851372327
0.09827151134447187
1.4789129918798913
---
0.375000000000000222044605
0.005000000000000000104083
-0.3501021197053552
0.09834891909985788
1.478912989691312
---
0.380000000000000226485497
0.005000000000000000104083
-0.35027439116644477
0.098426446428265
1.4789129874914881
---
0.385000000000000230926389
0.005000000000000000104083
-0.3504468833486222
0.09850409358895061
1.4789129852803764
---
0.390000000000000235367281
0.005000000000000000104083
-0.35061959670476167
0.09858186084189552
1.4789129830579324
---
0.395000000000000239808173
0.005000000000000000104083
-0.35079253168898583
0.09865974844781192
1.4789129808241135
---
0.400000000000000244249065
0.005000000000000000104083
-0.3509656887566699
0.09873775666814458
1.478912978578876
---

-0.36253151984227144
0.10399371326529208
1.478912809039339
---
0.725000000000000532907052
0.005000000000000000104083
-0.36272015283616854
0.10408015947587114
1.4789128059520233
---
0.730000000000000537347944
0.005000000000000000104083
-0.36290904096986976
0.10416674531127437
1.4789128028501104
---
0.735000000000000541788836
0.005000000000000000104083
-0.36309818479348965
0.10425347108835341
1.4789127997335425
---
0.740000000000000546229728
0.005000000000000000104083
-0.3632875848587346
0.10434033712489288
1.478912796602269
---
0.745000000000000550670620
0.005000000000000000104083
-0.36347724171890866
0.10442734373960912
1.4789127934562345
---
0.750000000000000555111512
0.005000000000000000104083
-0.36366715592891935
0.10451449125215996
1.4789127902953876
---
0.755000000000000559552404
0.005000000000000000104083
-0.3638573280452834
0.10460177998314352
1.4789127871196717
---
0.760000000000000563993297
0.005000000000000000104083
-0.3640477586261327
0.10468921025410392
1.478912783929035
--

-0.3767997639955924
0.1105946266725794
1.478912546086469
---
1.084999999999998854249839
0.005000000000000000104083
-0.3770082743856188
0.11069199500269411
1.4789125418017168
---
1.089999999999998747668428
0.005000000000000000104083
-0.37721708396374054
0.11078952837018634
1.47891253749809
---
1.094999999999998641087018
0.005000000000000000104083
-0.3774261934110446
0.11088722716859373
1.478912533175521
---
1.099999999999998534505607
0.005000000000000000104083
-0.3776356034106969
0.11098509179267324
1.4789125288339442
---
1.104999999999998427924197
0.005000000000000000104083
-0.3778453146479503
0.11108312263840436
1.4789125244732921
---
1.109999999999998321342787
0.005000000000000000104083
-0.3780553278101524
0.11118132010299431
1.4789125200934987
---
1.114999999999998214761376
0.005000000000000000104083
-0.3782656435867537
0.11127968458487925
1.4789125156944973
---
1.119999999999998108179966
0.005000000000000000104083
-0.37847626266931556
0.1113782164837355
1.4789125112762191
---
1.124

-0.3923885403837575
0.11794163602700933
1.4789121909842378
---
1.439999999999991286969703
0.005000000000000000104083
-0.3926201126635588
0.11805177439327114
1.4789121851831457
---
1.444999999999991180388292
0.005000000000000000104083
-0.3928520381463131
0.1181621090537138
1.4789121793579605
---
1.449999999999991073806882
0.005000000000000000104083
-0.39308431768271196
0.11827264050128374
1.4789121735085986
---
1.454999999999990967225472
0.005000000000000000104083
-0.393316952126192
0.11838336923054094
1.4789121676349797
---
1.459999999999990860644061
0.005000000000000000104083
-0.3935499423329458
0.11849429573765878
1.4789121617370198
---
1.464999999999990754062651
0.005000000000000000104083
-0.3937832891619332
0.11860542052043531
1.4789121558146392
---
1.469999999999990647481241
0.005000000000000000104083
-0.39401699347489233
0.11871674407829563
1.4789121498677524
---
1.474999999999990540899830
0.005000000000000000104083
-0.3942510561363509
0.11882826691230379
1.478912143896279
---
1.

...

-5.028349613923513e-07
-200.91586555798133
5.245253258338643e+25
---
7.826717611444459876679502
0.000012442823219219413040
-5.037931962906522e-07
-200.9074180367849
5.268403030619696e+25
---
7.826730054267678760027138
0.000012443346235942922209
-5.047525443168252e-07
-200.89897084177053
5.291647499288409e+25
---
7.826742497613914828491488
0.000012443869276445776841
-5.057130055520482e-07
-200.89052397292227
5.314987023425269e+25
---
7.826754941483191174711465
0.000012444392340729216993
-5.066745800775076e-07
-200.8820774302313
5.33842196339252e+25
---
7.826767385875531779504399
0.000012444915428473013388
-5.07637267974374e-07
-200.87363121368298
5.361952680837893e+25
---
7.826779830790960623687624
0.000012445438539995608062
-5.086010693238508e-07
-200.86518532326514
5.385579538700327e+25
---
7.826792276229500799900052
0.000012445961675302979376
-5.095659842071508e-07
-200.8567397589635
5.4093029012135225e+25
---
7.826804722191176288959014
0.000012446484834396325032
-5.105320127054955e-

-5.746778792573198e-07
-200.308476996167
7.176878452752723e+25
---
7.827614832965159585853598
0.000012480541225592528475
-5.757164673711092e-07
-200.30005292768985
7.207845318992046e+25
---
7.827627313506384965080542
0.000012481065956293181383
-5.76756174479874e-07
-200.29162918448438
7.238936287428916e+25
---
7.827639794572340825595802
0.000012481590710862856827
-5.777970006654241e-07
-200.2832057665354
7.270151821496138e+25
---
7.827652276163052036395129
0.000012482115489302749123
-5.788389460095787e-07
-200.27478267383523
7.3014923862621145e+25
---
7.827664758278541690117436
0.000012482640291614028870
-5.798820105941654e-07
-200.26635990636646
7.3329584484364766e+25
---
7.827677240918832879401634
0.000012483165117797986947
-5.809261945010209e-07
-200.25793746411986
7.36455047637551e+25
---
7.827689724083950473243476
0.000012483689967855761765
-5.819714978119906e-07
-200.2495153470824
7.396268940088044e+25
---
7.827702207773918452460293
0.000012484214841788617099
-5.830179206089288e-

-6.523212627728344e-07
-199.70277470770918
9.753100164337087e+25
---
7.828514774568842149449210
0.000012518382874275030535
-6.534406281554598e-07
-199.69437402656172
9.794290421622287e+25
---
7.828527292951716454183497
0.000012518909325351596976
-6.545611184459097e-07
-199.68597366977968
9.83564267801162e+25
---
7.828539811861041641805059
0.000012519435800387217084
-6.55682733726633e-07
-199.6775736373486
9.877157529967692e+25
---
7.828552331296841693131228
0.000012519962299383169879
-6.568054740800877e-07
-199.66917392925862
9.918835576036477e+25
---
7.828564851259141477157755
0.000012520488822340603938
-6.579293395887404e-07
-199.660774545493
9.96067741685386e+25
---
7.828577371747964086523552
0.000012521015369260801668
-6.590543303350671e-07
-199.65237548604338
1.0002683655153069e+26
---
7.828589892763333502045953
0.000012521541940144964163
-6.601804464015521e-07
-199.64397675089583
1.0044854895771559e+26
---
7.828602414305273704542287
0.000012522068534994292515
-6.613076878706893e-

-7.298098711188341e-07
-199.14064563863604
1.2901267450089426e+26
---
7.829354671352842132137084
0.000012553708097042223552
-7.310047880456452e-07
-199.13226666212552
1.2954735799513567e+26
---
7.829367225060939183833852
0.000012554236155062214550
-7.322008354240438e-07
-199.12388800913772
1.3008411069526826e+26
---
7.829379779297093833179133
0.000012554764237125037551
-7.333980133370792e-07
-199.11550967966062
1.3062294012744446e+26
---
7.829392334061330949168678
0.000012555292343231937692
-7.3459632186781e-07
-199.10713167368095
1.3116385384386467e+26
---
7.829404889353674512619818
0.000012555820473384143171


KeyboardInterrupt: 

In [7]:
rnpfile.close()
signpfile.close()
phinpfile.close()
massnpfile.close()

In [8]:
Nu=i+1

print(len(rnpf[0,:]))
print(len(rnpf))
print(Nu)
print(len(urange))
#print(len(rnp))
#rnpf[i+1][j+1]=answer[0]
#phinpf[i+1][j+1]=answer[1]
#signpf[i+1][j+1]=answer[2]
#massnpf[i+1][j+1]=answer[3]
#drunp[i+1][j+1]=answer[4]
#dsigunp[i+1][j+1]=answer[5]

4000
2
39737
39737


In [9]:
#print(rnpf[1,0])

In [10]:
#print(dnu.x4giveralt(0,0,du,dv,rnpf,phinpf,signpf,Q,Lambda))

In [11]:
#print(rnpf)

In [12]:
vrange=np.arange(0,vmax,dv0)
#print(urange)

In [13]:
switch=0.0
np.save('rnputil',np.array([Nu*Nv,Nu,Nv,ru0,dr0v,M0,Q,Lambda,wHD,switch]))
np.save('urange',urange)
np.save('vrange',vrange)

In [14]:
stop = timeit.default_timer()

In [15]:
acttime=stop - start

numpoints=Nu*Nv



print(str(acttime)+' seconds')
print(str((acttime)/60)+' minutes')
print(str((acttime)/3600)+' hours')

print(str(numpoints)+' points')

print(str((numpoints)/(stop - start))+' points per second') 

exttimef=(acttime-predtime)/60

exttime=format(abs((acttime-predtime)/60),'.2f')
if exttimef>0.0:
    print("Took "+str(exttime)+" more minutes")
if exttimef<0.0:
    print("Took "+str(exttime)+" less minutes")
if exttimef==0.0:
    print("Took exactly the right time!!!!")

1395.503179770999 seconds
23.25838632951665 minutes
0.38763977215861084 hours
158948000 points
113900.13459237208 points per second
Took 198.96 less minutes


conv=False
j=0
tempanswer=[]
    while conv==False:
        dv=TempTolv*dv0
        jcount=1
        while j<Nv-1:
            j1=mth.ceil(jcount*TempTolv)
            j2=mth.floor(jcount*TempTolv)
            answer=dnu.x4giveralt(0,j+mth.ceil((jcount-1)*TempTolv),du,dv*TempTolv,rnpf,phinpf,signpf,massnpf,M0,Q,Lambda,datatype)
            rnpf[1][j+j1]=answer[0]
            phinpf[1][j+j1]=answer[1]
            signpf[1][j+j1]=answer[2]
            massnpf[1][j+j1]=answer[3]
            #drunptemp[j+1]=answer[4]
            dsigunpv=answer[5]
            jcount=(jcount+1)**(0**j2)
            j=j+j2
        
        if np.abs(tempanswer[0]-answer[0])/answer[0]>0.01 or not tempanswer:
            tempanswer=answer
            TempTol=TempTolv/2
            
        else:
            conv=True
            